## Env

In [1]:
!pip install lightning

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 819.0/819.0 kB 22.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 70.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 76.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 47.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 19.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 109.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 962.5/962.5 kB 70.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
from google.colab import drive
drive.mount("/content/drive/")

Mounted at /content/drive/


In [3]:
!unzip -qq "/content/drive/MyDrive/MAGISTERKA/datasets/fog-combined.zip" -d "/content/datasets/"

## Setup

In [4]:
from pathlib import Path
from time import time

import lightning as L
from lightning.pytorch.loggers import TensorBoardLogger

import torch
from torchvision.models import get_weight
from torchvision.transforms import v2

In [5]:
base_transform = v2.Compose([
    v2.Resize((256, 256), v2.InterpolationMode.BILINEAR),
    v2.CenterCrop((224, 224)),
    v2.ToImage(),
    v2.ToDtype(torch.float32, scale=True),
])
transforms = {
    "grayscale": v2.Compose([
        base_transform,
        v2.Grayscale(num_output_channels=3)
    ]),
    "color": v2.Compose([
        base_transform,
    ]),
}

In [6]:
BASE_PATH = Path("/content")
DRIVE_PATH = Path("/content/drive/MyDrive/MAGISTERKA")
SAVE_DIR = DRIVE_PATH / "lightning_logs/runs/classify"

In [7]:
import sys
sys.path.insert(0, str(DRIVE_PATH / 'src'))
from cnn_model import CNNClassifier, get_dataloader

In [8]:
DATASET_PATHS = {
    'fog-detection': BASE_PATH / 'datasets/fog-detection-dataset-prepared',
    'fog-or-smog': BASE_PATH / 'datasets/fog-or-smog-detection-dataset-prepared',
    'foggy-cityscapes': BASE_PATH / 'datasets/foggy-cityscapes-image-dataset-prepared',
    'combined': BASE_PATH / 'datasets/fog-combined',
}

In [9]:
DATASET_NORMALIZATION = {
    'fog-detection': {'mean': [0.4850, 0.5044, 0.4878], 'std': [0.2631, 0.2524, 0.2793]},
    'fog-or-smog': {'mean': [0.5411, 0.5339, 0.5088], 'std': [0.2353, 0.2157, 0.2289]},
    'foggy-cityscapes': {'mean': [0.4169, 0.4507, 0.4173], 'std': [0.1860, 0.1835, 0.1820]},
    'combined': {'mean': [0.5017, 0.5087, 0.4826], 'std': [0.2259, 0.2118, 0.2227]}
}

In [10]:
def get_dataset_stats(dataset_path: Path):
  dataset = get_dataloader(dataset_path, transforms["color"])
  # Calculate mean color and std
  mean = torch.zeros(3)
  std = torch.zeros(3)

  for images, _ in dataset:
    mean += images.mean(dim=(0, 2, 3))
    std += images.std(dim=(0, 2, 3))

  mean /= len(dataset)
  std /= len(dataset)

  return mean, std


In [11]:
# get_dataset_stats(DATASET_PATHS['fog-detection'])

In [12]:
# get_dataset_stats(DATASET_PATHS['fog-or-smog'])

In [13]:
# get_dataset_stats(DATASET_PATHS['foggy-cityscapes'])

In [14]:
# get_dataset_stats(DATASET_PATHS['combined'])

In [15]:
def _get_formatted_metric(values: list[float]):
  avg = sum(values) / len(values)
  std = (sum([(v - avg) ** 2 for v in values]) / len(values)) ** 0.5
  return f"{avg:.4f} ± {std:.4f}"

def run_model(
    run_name: str,
    model_name: str,
    dataset: str,
    version: int = 1,
    repeat: int = 5,
    transform: str = "color",
    normalize: bool = False
):
  save_dir = SAVE_DIR / run_name
  model = CNNClassifier(
      model_name=model_name,
      num_classes=2,
      weights=False,
  )
  _transform = transforms[transform]
  if normalize:
    _transform = v2.Compose([
        base_transform,
        v2.Normalize(**DATASET_NORMALIZATION[dataset])
    ])

  train_dataloaders=get_dataloader(
    path=DATASET_PATHS[dataset] / "train",
    transform=_transform,
    batch_size=32,
    shuffle=True,
    num_workers=2,
  )
  val_dataloaders=get_dataloader(
    path=DATASET_PATHS[dataset] / "val",
    transform=_transform,
    batch_size=32,
    shuffle=False,
    num_workers=2,
  )

  test_dataloader = {
      dataset_name: get_dataloader(path=path / "test", transform=_transform)
      for dataset_name, path in DATASET_PATHS.items()
  }

  final_res = {}
  training_times = []
  for i in range(repeat):
    trainer = L.Trainer(
        max_epochs=20,
        logger=L.pytorch.loggers.TensorBoardLogger(
            save_dir=save_dir,
            name=f"{model_name}-{dataset}-{transform}-{normalize}",
            version=f"{version}000{i+1:02}",
        ),
        callbacks=[
            L.pytorch.callbacks.early_stopping.EarlyStopping(
                monitor="val_loss", mode="min", patience=5, verbose=False
            ),
            L.pytorch.callbacks.ModelCheckpoint(
                monitor="val_f1",
                mode="max",
                dirpath=save_dir / f"{model_name}-{dataset}" / f"version_{version}",
                filename=f"{model_name}-{dataset}-{transform}-{normalize}",
            ),
        ],
        log_every_n_steps=1,
    )

    model = CNNClassifier(
      model_name=model_name,
      num_classes=2,
      weights=False,
    )
    _start = time()
    trainer.fit(
        model,
        train_dataloaders=train_dataloaders,
        val_dataloaders=val_dataloaders
    )
    _end = time()
    training_times.append(_end - _start)
    res = {
        dataset_name: trainer.test(
            model,  dataloader
        )[0]
        for dataset_name, dataloader in test_dataloader.items()
    }
    for dataset_name, metrics in res.items():
      if dataset_name not in final_res:
        final_res[dataset_name] = {}
      for metric_name, metric_value in metrics.items():
        if metric_name not in final_res[dataset_name]:
          final_res[dataset_name][metric_name] = []
        final_res[dataset_name][metric_name].append(metric_value)


  latex_table = [
    [
      dataset,
      # *[round(m, 4) for m in metrics.values()]
      # Add average value and std
      *[_get_formatted_metric(m) for m in metrics.values()]
    ] for dataset, metrics in final_res.items()
  ]
  latex_table_str = ""
  for line in latex_table:
    latex_table_str += " & ".join([str(l) for l in line]) + " \\\\\n"
  return latex_table_str


## ResNet18

In [ ]:
run_model(
  run_name="CNN-COLOR-TRUE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='color',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8232323527336121     │
│          test_f1          │    0.8444444537162781     │
│      test_precision       │    0.7539682388305664     │
│        test_recall        │    0.9595959782600403     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.9361979365348816     │
│          test_f1          │    0.9411764740943909     │
│      test_precision       │    0.9137529134750366     │
│        test_recall        │    0.9702970385551453     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9811 ± 0.0215 & 0.9845 ± 0.0176 & 0.9877 ± 0.0179 & 0.9815 ± 0.0226 \\\\\nfog-or-smog & 0.9733 ± 0.0029 & 0.9738 ± 0.0029 & 0.9864 ± 0.0049 & 0.9617 ± 0.0061 \\\\\nfoggy-cityscapes & 0.8596 ± 0.0233 & 0.8603 ± 0.0188 & 0.8647 ± 0.0554 & 0.8626 ± 0.0566 \\\\\ncombined & 0.9451 ± 0.0060 & 0.9474 ± 0.0052 & 0.9551 ± 0.0211 & 0.9406 ± 0.0174 \\\\\n'

In [ ]:
run_model(
  run_name="CNN-COLOR-FALSE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='color',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8232323527336121     │
│          test_f1          │    0.7904191613197327     │
│      test_precision       │     0.970588207244873     │
│        test_recall        │    0.6666666865348816     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │        0.93359375         │
│          test_f1          │    0.9341935515403748     │
│      test_precision       │    0.9757412672042847     │
│        test_recall        │     0.896039605140686     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9774 ± 0.0228 & 0.9817 ± 0.0184 & 0.9759 ± 0.0226 & 0.9877 ± 0.0179 \\\\\nfog-or-smog & 0.9668 ± 0.0026 & 0.9677 ± 0.0026 & 0.9739 ± 0.0053 & 0.9617 ± 0.0081 \\\\\nfoggy-cityscapes & 0.8303 ± 0.0216 & 0.8194 ± 0.0413 & 0.8749 ± 0.0758 & 0.7939 ± 0.1326 \\\\\ncombined & 0.9331 ± 0.0051 & 0.9355 ± 0.0066 & 0.9484 ± 0.0257 & 0.9248 ± 0.0349 \\\\\n'

In [ ]:
run_model(
  run_name="CNN-GRAYSCALE-TRUE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8888888955116272     │
│          test_f1          │    0.8877550959587097     │
│      test_precision       │    0.8969072103500366     │
│        test_recall        │    0.8787878751754761     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │         0.953125          │
│          test_f1          │    0.9549999833106995     │
│      test_precision       │    0.9646464586257935     │
│        test_recall        │    0.9455445408821106     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9868 ± 0.0128 & 0.9894 ± 0.0101 & 0.9793 ± 0.0195 & 1.0000 ± 0.0000 \\\\\nfog-or-smog & 0.9716 ± 0.0046 & 0.9721 ± 0.0046 & 0.9846 ± 0.0034 & 0.9600 ± 0.0086 \\\\\nfoggy-cityscapes & 0.8505 ± 0.0316 & 0.8437 ± 0.0412 & 0.8752 ± 0.0232 & 0.8202 ± 0.0863 \\\\\ncombined & 0.9424 ± 0.0093 & 0.9444 ± 0.0098 & 0.9575 ± 0.0086 & 0.9322 ± 0.0241 \\\\\n'

In [ ]:
run_model(
  run_name="CNN-GRAYSCALE-FALSE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

## Swin_S

In [ ]:
run_model(
  run_name="CNN-COLOR-TRUE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='color',
  normalize=True
)

In [ ]:
run_model(
  run_name="CNN-COLOR-FALSE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='color',
  normalize=False
)

In [ ]:
run_model(
  run_name="CNN-GRAYSCALE-TRUE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=True
)

In [16]:
run_model(
  run_name="CNN-GRAYSCALE-FALSE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | SwinTransformer  | 48.8 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.7070707082748413     │
│          test_f1          │    0.7363636493682861     │
│      test_precision       │    0.6694214940071106     │
│        test_recall        │    0.8181818127632141     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.7669270634651184     │
│          test_f1          │    0.7765293121337891     │
│      test_precision       │    0.7833753228187561     │
│        test_recall        │    0.7698019742965698     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.7170 ± 0.1027 & 0.7096 ± 0.1278 & 0.9063 ± 0.0548 & 0.5938 ± 0.1525 \\\\\nfog-or-smog & 0.8534 ± 0.0185 & 0.8602 ± 0.0169 & 0.8514 ± 0.0336 & 0.8708 ± 0.0300 \\\\\nfoggy-cityscapes & 0.7020 ± 0.0385 & 0.6345 ± 0.1126 & 0.8280 ± 0.1104 & 0.5636 ± 0.1929 \\\\\ncombined & 0.7956 ± 0.0217 & 0.7937 ± 0.0250 & 0.8479 ± 0.0466 & 0.7510 ± 0.0579 \\\\\n'

## EfficientNet B1

In [ ]:
run_model(
  run_name="CNN-COLOR-TRUE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='color',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | EfficientNet     | 6.5 M  | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │     0.808080792427063     │
│          test_f1          │     0.808080792427063     │
│      test_precision       │     0.808080792427063     │
│        test_recall        │     0.808080792427063     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.9192708134651184     │
│          test_f1          │    0.9240196347236633     │
│      test_precision       │    0.9150485396385193     │
│        test_recall        │    0.9331682920455933     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9736 ± 0.0139 & 0.9790 ± 0.0108 & 0.9591 ± 0.0206 & 1.0000 ± 0.0000 \\\\\nfog-or-smog & 0.9586 ± 0.0079 & 0.9604 ± 0.0072 & 0.9535 ± 0.0152 & 0.9675 ± 0.0031 \\\\\nfoggy-cityscapes & 0.7980 ± 0.0280 & 0.8124 ± 0.0173 & 0.7654 ± 0.0502 & 0.8707 ± 0.0391 \\\\\ncombined & 0.9193 ± 0.0059 & 0.9252 ± 0.0050 & 0.9028 ± 0.0124 & 0.9490 ± 0.0092 \\\\\n'

In [ ]:
run_model(
  run_name="CNN-COLOR-FALSE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='color',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | EfficientNet     | 6.5 M  | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.7929292917251587     │
│          test_f1          │    0.8127853870391846     │
│      test_precision       │    0.7416666746139526     │
│        test_recall        │    0.8989899158477783     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │         0.921875          │
│          test_f1          │    0.9277108311653137     │
│      test_precision       │    0.9037558436393738     │
│        test_recall        │    0.9529703259468079     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9717 ± 0.0060 & 0.9775 ± 0.0046 & 0.9560 ± 0.0089 & 1.0000 ± 0.0000 \\\\\nfog-or-smog & 0.9642 ± 0.0077 & 0.9653 ± 0.0074 & 0.9674 ± 0.0072 & 0.9633 ± 0.0085 \\\\\nfoggy-cityscapes & 0.7929 ± 0.0064 & 0.8086 ± 0.0077 & 0.7543 ± 0.0324 & 0.8768 ± 0.0576 \\\\\ncombined & 0.9211 ± 0.0031 & 0.9267 ± 0.0028 & 0.9067 ± 0.0137 & 0.9480 ± 0.0157 \\\\\n'

In [18]:
run_model(
  run_name="CNN-GRAYSCALE-TRUE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | EfficientNet     | 6.5 M  | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.7222222089767456     │
│          test_f1          │    0.7791164517402649     │
│      test_precision       │    0.6466666460037231     │
│        test_recall        │    0.9797979593276978     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │        0.87890625         │
│          test_f1          │    0.8949152827262878     │
│      test_precision       │    0.8232848048210144     │
│        test_recall        │    0.9801980257034302     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9547 ± 0.0173 & 0.9646 ± 0.0131 & 0.9319 ± 0.0243 & 1.0000 ± 0.0000 \\\\\nfog-or-smog & 0.9591 ± 0.0143 & 0.9609 ± 0.0131 & 0.9526 ± 0.0253 & 0.9700 ± 0.0148 \\\\\nfoggy-cityscapes & 0.7919 ± 0.0450 & 0.8100 ± 0.0263 & 0.7616 ± 0.0754 & 0.8768 ± 0.0583 \\\\\ncombined & 0.9154 ± 0.0216 & 0.9226 ± 0.0173 & 0.8965 ± 0.0409 & 0.9520 ± 0.0182 \\\\\n'

In [19]:
run_model(
  run_name="CNN-GRAYSCALE-FALSE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | EfficientNet     | 6.5 M  | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8282828330993652     │
│          test_f1          │    0.8454545736312866     │
│      test_precision       │    0.7685950398445129     │
│        test_recall        │     0.939393937587738     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8971354365348816     │
│          test_f1          │    0.9073857069015503     │
│      test_precision       │    0.8619153499603271     │
│        test_recall        │    0.9579207897186279     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9528 ± 0.0198 & 0.9632 ± 0.0151 & 0.9294 ± 0.0282 & 1.0000 ± 0.0000 \\\\\nfog-or-smog & 0.9254 ± 0.0115 & 0.9285 ± 0.0101 & 0.9235 ± 0.0248 & 0.9342 ± 0.0148 \\\\\nfoggy-cityscapes & 0.7869 ± 0.0266 & 0.8051 ± 0.0243 & 0.7423 ± 0.0263 & 0.8808 ± 0.0396 \\\\\ncombined & 0.8935 ± 0.0108 & 0.9021 ± 0.0088 & 0.8748 ± 0.0203 & 0.9317 ± 0.0146 \\\\\n'